In [3]:
import os
import re
from tqdm.notebook import tqdm  # Use this version in Colab for cleaner output
from bs4 import BeautifulSoup
from requests import get
from urllib.parse import urljoin,unquote
from concurrent.futures import ThreadPoolExecutor, as_completed
import csv
from google.colab import drive
drive.mount('/content/drive')


Mounted at /content/drive


In [ ]:
ChampionData = []
url = "https://wiki.leagueoflegends.com/"

response = get(f"{url}/en-us")
if response.ok:
    soup = BeautifulSoup(response.text, "html.parser")
    grid = soup.find("div", id="champion-grid")

    if grid:
        links = grid.find_all("a", href=True)

        for a_tag in tqdm(links, desc="Parsing champion links"):
            href = a_tag["href"]

            # Decode and format the champion name
            name = href.rstrip("/").split("/")[-1]
            # Add to dictionary
            ChampionData.append(name)

    else:
        print("Champion grid not found.")
else:
    print(f"Failed to load page: {response.status_code}")
for name in ChampionData:
  print(name)


Parsing champion links: 100%|██████████| 171/171 [00:00<00:00, 212197.04it/s]

Aatrox
Ahri
Akali
Akshan
Alistar
Ambessa
Amumu
Anivia
Annie
Aphelios
Ashe
Aurelion_Sol
Aurora
Azir
Bard
Bel%27Veth
Blitzcrank
Brand
Braum
Briar
Caitlyn
Camille
Cassiopeia
Cho%27Gath
Corki
Darius
Diana
Dr._Mundo
Draven
Ekko
Elise
Evelynn
Ezreal
Fiddlesticks
Fiora
Fizz
Galio
Gangplank
Garen
Gnar
Gragas
Graves
Gwen
Hecarim
Heimerdinger
Hwei
Illaoi
Irelia
Ivern
Janna
Jarvan_IV
Jax
Jayce
Jhin
Jinx
K%27Sante
Kai%27Sa
Kalista
Karma
Karthus
Kassadin
Katarina
Kayle
Kayn
Kennen
Kha%27Zix
Kindred
Kled
Kog%27Maw
LeBlanc
Lee_Sin
Leona
Lillia
Lissandra
Lucian
Lulu
Lux
Malphite
Malzahar
Maokai
Master_Yi
Mel
Milio
Miss_Fortune
Mordekaiser
Morgana
Naafiri
Nami
Nasus
Nautilus
Neeko
Nidalee
Nilah
Nocturne
Nunu_%26_Willump
Olaf
Orianna
Ornn
Pantheon
Poppy
Pyke
Qiyana
Quinn
Rakan
Rammus
Rek%27Sai
Rell
Renata_Glasc
Renekton
Rengar
Riven
Rumble
Ryze
Samira
Sejuani
Senna
Seraphine
Sett
Shaco
Shen
Shyvana
Singed
Sion
Sivir
Skarner
Smolder
Sona
Soraka
Swain
Sylas
Syndra
Tahm_Kench
Taliyah
Talon
Taric
Teemo
Thre

In [ ]:
output_dir = "/content/drive/My Drive/LeagueWikiScrape/"
os.makedirs(output_dir, exist_ok=True)

file_path = os.path.join(output_dir, "champion_names.csv")

with open(file_path, "w", newline='', encoding="utf-8") as f:
    writer = csv.writer(f)
    writer.writerow(["Champion"])  # header

    for name in ChampionData:
        writer.writerow([name])

In [ ]:
url_base = "https://wiki.leagueoflegends.com/en-us"
CosmeticsLinks = {}
paren_pattern = re.compile(r"\s*\([^)]*\)")
max_threads = 10  # adjust based on system

def scrape_champion_cosmetics(champ_name):
    local_links = {}
    try:
        response = get(f"{url_base}/{champ_name}/Cosmetics")
        if not response.ok:
            return champ_name, None, f"[!] Failed to load cosmetics page for {champ_name}"

        soup = BeautifulSoup(response.text, "html.parser")
        divs = soup.find_all("div", style="font-size:small")
        if not divs:
            return champ_name, None, f"[=] No cosmetics found for {champ_name}"

        skins_dir = os.path.join("Champions", champ_name, "skins")
        os.makedirs(skins_dir, exist_ok=True)

        skin_blocks = []
        for div in divs:
            skin_blocks.extend(div.select('div[style*="display:inline-block"]'))

        for item in skin_blocks:
            name_div = item.select_one('div[style*="float:left"]')
            skin_name = name_div.find(string=True, recursive=False).strip() if name_div else None
            skin_name = paren_pattern.sub("", skin_name).strip()

            file_link_tag = item.select_one('a.mw-file-description[href]')
            href = file_link_tag["href"].split('/')[-1] if file_link_tag else None

            if skin_name and href:
                local_links[skin_name] = href

        return champ_name, local_links, None

    except Exception as e:
        return champ_name, None, f"[!] Error processing {champ_name}: {e}"

# Multithreaded execution
with ThreadPoolExecutor(max_workers=max_threads) as executor:
    futures = {executor.submit(scrape_champion_cosmetics, name): name for name in ChampionData}
    for future in tqdm(as_completed(futures), total=len(futures), desc="Scraping Champions", unit="champ"):
        champ_name, data, error = future.result()
        if error:
            tqdm.write(error)
        elif data:
            CosmeticsLinks[champ_name] = data

output_dir = "/content/drive/My Drive/LeagueWikiScrape/"
os.makedirs(output_dir, exist_ok=True)

file_path = os.path.join(output_dir, "cosmetic_links.csv")

with open(file_path, "w", newline='', encoding="utf-8") as f:
    writer = csv.writer(f)
    writer.writerow(["Champion", "Skin", "Image URL"])

    for champ, skins in CosmeticsLinks.items():
        for raw_skin, href in skins.items():
            # Remove champ name from skin if it ends with it (e.g., "Spirit Blossom Ahri" -> "Spirit Blossom")
            suffix = f" {champ}"
            if raw_skin.endswith(suffix):
                skin = raw_skin.removesuffix(suffix)
            else:
                skin = raw_skin

            # Handle relative or absolute URL
            full_url = f"https://wiki.leagueoflegends.com{href}" if href.startswith("/") else href
            writer.writerow([champ, skin, full_url])


In [ ]:
from bs4 import BeautifulSoup
from requests import get
from concurrent.futures import ThreadPoolExecutor, as_completed
from tqdm import tqdm

BASE_URL = "https://wiki.leagueoflegends.com/en-us"
CATEGORIES = ["Splashes", "Loading", "Circles", "Squares", "Centered", "Tiles"]

def scrape_champion(champ_name, skins):
    champion_data = {}
    for skin_name, skin_path in skins.items():
        try:
            response = get(f"{BASE_URL}/{skin_path}", timeout=10)
            soup = BeautifulSoup(response.text, "html.parser")
        except Exception as e:
            print(f"[ERROR] {champ_name} - {skin_name}: {e}")
            continue

        skin_data = {}

        for category in CATEGORIES:
            div = soup.find("div", {"data-title": category})
            if not div:
                continue

            images = {}
            for a in div.find_all("a"):
                title = a.get("title")
                href = a.get("href")
                if title and href:
                    images[title] = href.split("/")[-1].split(":")[-1]

            if images:
                skin_data[category] = images

        if skin_data:
            champion_data[skin_name] = skin_data

    return champ_name, champion_data

# --- Run with multithreading ---
champion_results = {}

with ThreadPoolExecutor(max_workers=8) as executor:
    futures = [
        executor.submit(scrape_champion, champ_name, CosmeticsLinks[champ_name])
        for champ_name in CosmeticsLinks
    ]

    for future in tqdm(as_completed(futures), total=len(futures), desc="Scraping Champions"):
        champ_name, data = future.result()
        champion_results[champ_name] = data

# `champion_results` now holds all the scraped data
output_path = "/content/drive/My Drive/LeagueWikiScrape/champion_images.csv"

with open(output_path, "w", newline='', encoding='utf-8') as csvfile:
    writer = csv.writer(csvfile)
    writer.writerow(["Champion", "Skin", "Category", "Image Title", "Image URL Fragment"])

    for champ_name, skins in champion_results.items():
        for raw_skin_name, categories in skins.items():
            suffix = f" {champ_name}"
            if raw_skin_name.endswith(suffix):
                skin_name = raw_skin_name.removesuffix(suffix)
            else:
                skin_name = raw_skin_name

            for category, images in categories.items():
                for title, url_fragment in images.items():
                    writer.writerow([champ_name, skin_name, category, title, url_fragment])


Scraping Champions: 100%|██████████| 171/171 [00:58<00:00,  2.92it/s]


In [ ]:
import os
import requests
import hashlib
from tqdm import tqdm
from concurrent.futures import ThreadPoolExecutor, as_completed

# Config
base_url = "https://wiki.leagueoflegends.com/en-us/images/"
output_dir = "/content/drive/My Drive/LeagueWikiScrape/data"
max_threads = 10

# Helper: compute SHA256 hash of a file or bytes
def compute_hash(data):
    hasher = hashlib.sha256()
    hasher.update(data)
    return hasher.hexdigest()

def compute_file_hash(path):
    with open(path, 'rb') as f:
        return compute_hash(f.read())

# Download with local hash check
def download_image_if_changed(image_url, save_path):
    try:
        # Check if file exists
        if os.path.exists(save_path):
            local_hash = compute_file_hash(save_path)
        else:
            local_hash = None

        # Download image into memory
        response = requests.get(image_url, stream=True, timeout=15)
        response.raise_for_status()
        content = b''.join(response.iter_content(chunk_size=8192))
        remote_hash = compute_hash(content)

        if local_hash and local_hash == remote_hash:
            print(f"✅ Skipped (unchanged): {image_url}")
            return

        # Save new or changed file
        with open(save_path, 'wb') as f:
            f.write(content)
        print(f"⬇️ Downloaded: {image_url}")

    except Exception as e:
        print(f"❌ Error: {image_url} – {e}")

# === Run threaded download tasks ===
futures = []
with ThreadPoolExecutor(max_workers=max_threads) as executor:
    for champ_name, skins in tqdm(champion_results.items(), desc="Champions", unit="champ"):
        for skin_name, categories in skins.items():
            for category, image_data in categories.items():
                if not isinstance(image_data, dict):
                    continue

                folder_path = os.path.join(output_dir, champ_name, skin_name, category)
                os.makedirs(folder_path, exist_ok=True)

                for version_label, filename in image_data.items():
                    image_url = base_url + filename
                    ext = os.path.splitext(filename)[1]
                    safe_name = version_label.replace(" ", "_").replace("/", "-") + ext
                    save_path = os.path.join(folder_path, safe_name)

                    futures.append(executor.submit(download_image_if_changed, image_url, save_path))

    for _ in tqdm(as_completed(futures), total=len(futures), desc="Processing images", unit="img"):
        pass

print("🎉 Done. Only changed or new images were downloaded.")


In [ ]:
import os
import csv
import hashlib
import requests
from bs4 import BeautifulSoup
from urllib.parse import urljoin
from concurrent.futures import ThreadPoolExecutor, as_completed
from tqdm import tqdm

# === CONFIG ===
base_url = "https://wiki.leagueoflegends.com/en-us/{}/Audio"
site_root = "https://wiki.leagueoflegends.com"
output_dir = "/content/drive/MyDrive/LeagueWikiScrape/data"
max_threads = 10

# === HELPERS ===
def sanitize(text):
    return text.replace(" ", "_").replace("/", "-").replace('"', "").replace("'", "").strip()

def compute_hash(data):
    return hashlib.sha256(data).hexdigest()

def compute_file_hash(path):
    with open(path, 'rb') as f:
        return compute_hash(f.read())

# === DOWNLOAD FUNCTION ===
def download_audio(champ_name, category, subcategory, mwtitle, quote_text, audio_url, csv_map):
    filename = sanitize(mwtitle)
    folder = os.path.join(output_dir, champ_name, "audio", sanitize(category), sanitize(subcategory or ""))
    os.makedirs(folder, exist_ok=True)
    save_path = os.path.join(folder, filename)

    try:
        # Download into memory
        r = requests.get(audio_url, stream=True, timeout=15)
        r.raise_for_status()
        content = b''.join(r.iter_content(8192))
        remote_hash = compute_hash(content)

        # Compare hash if file exists
        if os.path.exists(save_path):
            local_hash = compute_file_hash(save_path)
            if local_hash == remote_hash:
                print(f"✅ Skipped (unchanged): {filename}")
            else:
                with open(save_path, 'wb') as f:
                    f.write(content)
                print(f"⬇️ Updated: {filename}")
        else:
            with open(save_path, 'wb') as f:
                f.write(content)
            print(f"⬇️ Downloaded: {filename}")

        # Add to CSV mapping
        csv_map.append({
            "Download Filename": filename,
            "Quote Text": quote_text,
            "Category": category,
            "Subcategory": subcategory or "",
            "URL": audio_url
        })

    except Exception as e:
        print(f"❌ Failed: {filename} - {e}")

# === COLLECT TASKS ===
tasks = []
csv_mappings = {}  # champ_name -> list of dicts

for champ in tqdm(ChampionData, desc="Parsing champions"):
    csv_mappings[champ] = []

    try:
        res = requests.get(base_url.format(champ))
        res.raise_for_status()
        soup = BeautifulSoup(res.text, "html.parser")

        content_div = soup.find("div", id="mw-content-text")
        current_category = "Uncategorized"
        current_subcategory = None

        for element in content_div.find_all(["h2", "h3", "ul"], recursive=True):
            if element.name == "h2":
                headline = element.find("span", class_="mw-headline")
                current_category = headline.get_text(strip=True) if headline else element.get_text(strip=True)
                current_subcategory = None

            elif element.name == "h3":
                headline = element.find("span", class_="mw-headline")
                if headline and headline.get("id", "").startswith("Using_"):
                    span = headline.find("span", {"style": "white-space:normal;"})
                    link = span.find("a") if span else None
                    if link:
                        current_subcategory = link.get_text(strip=True)
                    else:
                        current_subcategory = headline.get_text(strip=True).replace("Using", "").strip()
                else:
                    current_subcategory = None

            elif element.name == "ul":
                for li in element.find_all("li"):
                    quote_tag = li.find("i")
                    if not quote_tag:
                        continue
                    quote = quote_tag.get_text(strip=True)

                    for audio_tag in li.find_all("audio"):
                        mwtitle = audio_tag.get("data-mwtitle", "")
                        if "Original" not in mwtitle:
                            continue

                        source = audio_tag.find("source")
                        if not source:
                            continue
                        src = source.get("src", "")
                        if not src:
                            continue

                        audio_url = urljoin(site_root, src.split("?")[0])
                        tasks.append((
                            champ, current_category, current_subcategory,
                            mwtitle, quote, audio_url, csv_mappings[champ]
                        ))

    except Exception as e:
        print(f"❌ Error parsing {champ}: {e}")

# === MULTITHREADED DOWNLOAD ===
with ThreadPoolExecutor(max_workers=max_threads) as executor:
    futures = [
        executor.submit(download_audio, champ, cat, subcat, mwtitle, quote, url, mapping)
        for champ, cat, subcat, mwtitle, quote, url, mapping in tasks
    ]
    for _ in tqdm(as_completed(futures), total=len(futures), desc="Downloading audio", unit="file"):
        pass

# === WRITE CSVs ===
for champ, mapping in csv_mappings.items():
    if not mapping:
        continue
    csv_folder = os.path.join(output_dir, champ)
    os.makedirs(csv_folder, exist_ok=True)
    csv_path = os.path.join(csv_folder, "audio_mapping.csv")

    with open(csv_path, "w", newline="", encoding="utf-8") as f:
        writer = csv.DictWriter(f, fieldnames=["Download Filename", "Quote Text", "Category", "Subcategory", "URL"])
        writer.writeheader()
        writer.writerows(mapping)

print("🎉 All audio downloads and mappings complete.")


Parsing champions:  56%|█████▌    | 96/171 [00:46<00:18,  4.11it/s]

❌ Error parsing Nunu_%26_Willump: 404 Client Error: Not Found for url: https://wiki.leagueoflegends.com/en-us/Nunu_%26_Willump/Audio


Parsing champions: 100%|██████████| 171/171 [01:20<00:00,  2.13it/s]


✅ Skipped (unchanged): Aatrox_Original_Move_0.ogg
✅ Skipped (unchanged): Aatrox_Original_MoveFirstPantheon_2.ogg
✅ Skipped (unchanged): Aatrox_Original_Move_2.ogg
✅ Skipped (unchanged): Aatrox_Original_MoveFirstPantheon_0.ogg
✅ Skipped (unchanged): Aatrox_Original_Move_1.ogg
✅ Skipped (unchanged): Aatrox_Original_Move_3.ogg
✅ Skipped (unchanged): Aatrox_Original_Move_4.ogg
✅ Skipped (unchanged): Aatrox_Original_MoveFirstPantheon_1.ogg
✅ Skipped (unchanged): Aatrox_Original_Move_10.ogg
✅ Skipped (unchanged): Aatrox_Original_Move_8.ogg
✅ Skipped (unchanged): Aatrox_Original_Move_9.ogg
✅ Skipped (unchanged): Aatrox_Original_Move_7.ogg
✅ Skipped (unchanged): Aatrox_Original_Move_5.ogg
✅ Skipped (unchanged): Aatrox_Original_Move_11.ogg
✅ Skipped (unchanged): Aatrox_Original_Move_6.ogg
✅ Skipped (unchanged): Aatrox_Original_Move_12.ogg
✅ Skipped (unchanged): Aatrox_Original_Move_13.ogg
✅ Skipped (unchanged): Aatrox_Original_Move_14.ogg
✅ Skipped (unchanged): Aatrox_Original_Move_18.ogg
✅ Ski

✅ Skipped (unchanged): Aatrox_Original_MoveLong_2.ogg
✅ Skipped (unchanged): Aatrox_Original_MoveLong_4.ogg
✅ Skipped (unchanged): Aatrox_Original_MoveLong_3.ogg
✅ Skipped (unchanged): Aatrox_Original_MoveLong_6.ogg
✅ Skipped (unchanged): Aatrox_Original_MoveLong_10.ogg
✅ Skipped (unchanged): Aatrox_Original_MoveLong_9.ogg
✅ Skipped (unchanged): Aatrox_Original_MoveLong_13.ogg
✅ Skipped (unchanged): Aatrox_Original_MoveLong_12.ogg
✅ Skipped (unchanged): Aatrox_Original_MoveLong_7.ogg
✅ Skipped (unchanged): Aatrox_Original_MoveLong_11.ogg
✅ Skipped (unchanged): Aatrox_Original_MoveLong_8.ogg
✅ Skipped (unchanged): Aatrox_Original_MoveLong_14.ogg
✅ Skipped (unchanged): Aatrox_Original_MoveLong_15.ogg
✅ Skipped (unchanged): Aatrox_Original_MoveLong_17.ogg


...

⬇️ Downloaded: Zyra_Original_Move_2.ogg
⬇️ Downloaded: Zoe_Original_KillLux_4.ogg
⬇️ Downloaded: Zoe_Original_Death_1.ogg
⬇️ Downloaded: Zyra_Original_Taunt_1.ogg
⬇️ Downloaded: Zyra_Original_Move_4.ogg
⬇️ Downloaded: Zoe_Original_Death_3.ogg
⬇️ Downloaded: Zyra_Original_Taunt_0.ogg
⬇️ Downloaded: Zyra_Original_Joke_0.ogg
⬇️ Downloaded: Zyra_Original_Laugh_2.ogg
⬇️ Downloaded: Zyra_Original_Joke_1.ogg
⬇️ Downloaded: Zyra_Original_Laugh_1.ogg
⬇️ Downloaded: Zyra_Original_BasicAttack_1.ogg
⬇️ Downloaded: Zyra_Original_Laugh_0.ogg
⬇️ Downloaded: Zyra_Original_BasicAttack_0.ogg
⬇️ Downloaded: Zyra_Original_BasicAttack_2.ogg


⬇️ Downloaded: Zyra_Original_BasicAttack_3.ogg
⬇️ Downloaded: Zyra_Original_Attack_4.ogg
⬇️ Downloaded: Zyra_Original_Attack_2.ogg
⬇️ Downloaded: Zyra_Original_Attack_1.ogg
⬇️ Downloaded: Zyra_Original_Attack_5.ogg
⬇️ Downloaded: Zyra_Original_Attack_0.ogg
⬇️ Downloaded: Zyra_Original_Attack_3.ogg
⬇️ Downloaded: Zyra_Original_Q_1.ogg
⬇️ Downloaded: Zyra_Original_Q_2.ogg
⬇️ Downloaded: Zyra_Original_Q_0.ogg
⬇️ Downloaded: Zyra_Original_QPlant_0.ogg


⬇️ Downloaded: Zyra_Original_Q_3.ogg
⬇️ Downloaded: Zyra_Original_W_3.ogg
⬇️ Downloaded: Zyra_Original_QPlant_3.ogg
⬇️ Downloaded: Zyra_Original_W_2.ogg
⬇️ Downloaded: Zyra_Original_QPlant_2.ogg
⬇️ Downloaded: Zyra_Original_W_0.ogg
⬇️ Downloaded: Zyra_Original_QPlant_1.ogg
⬇️ Downloaded: Zyra_Original_E_0.ogg
⬇️ Downloaded: Zyra_Original_E_1.ogg
⬇️ Downloaded: Zyra_Original_W_1.ogg
⬇️ Downloaded: Zyra_Original_E_3.ogg
⬇️ Downloaded: Zyra_Original_EPlant_0.ogg


⬇️ Downloaded: Zyra_Original_R_0.ogg
⬇️ Downloaded: Zyra_Original_EPlant_2.ogg
⬇️ Downloaded: Zyra_Original_R_1.ogg
⬇️ Downloaded: Zyra_Original_E_2.ogg
⬇️ Downloaded: Zyra_Original_Death_0.ogg
⬇️ Downloaded: Zyra_Original_EPlant_1.ogg
⬇️ Downloaded: Zyra_Original_R_2.ogg
⬇️ Downloaded: Zyra_Original_Death_1.ogg
⬇️ Downloaded: Zyra_Original_R_3.ogg
⬇️ Downloaded: Zyra_Original_EPlant_3.ogg
⬇️ Downloaded: Zyra_Original_Death_3.ogg
⬇️ Downloaded: Zyra_Original_Death_2.ogg
⬇️ Downloaded: Zyra_Original_Taunt_1.ogg


🎉 All audio downloads and mappings complete.


In [31]:
import os
import csv
import requests
from bs4 import BeautifulSoup
from urllib.parse import urljoin
from tqdm import tqdm
import hashlib
from concurrent.futures import ThreadPoolExecutor, as_completed

# === Config ===
base_url = "https://wiki.leagueoflegends.com/en-us/"
output_dir = "/content/drive/MyDrive/LeagueWikiScrape/data"
skills = ["skill_innate", "skill_q", "skill_w", "skill_e", "skill_r"]
MAX_THREADS = 10

# === Helper Functions ===
def sanitize(text):
    return text.replace(" ", "_").replace("/", "-").replace('"', "").replace("'", "").strip()

def compute_hash(data):
    return hashlib.sha256(data).hexdigest()

def compute_file_hash(path):
    with open(path, 'rb') as f:
        return compute_hash(f.read())

def download_image_if_not_exists(url, save_path, session):
    try:
        r = session.get(url, stream=True, timeout=10)
        r.raise_for_status()
        content = b''.join(r.iter_content(8192))
        remote_hash = compute_hash(content)

        if os.path.exists(save_path):
            local_hash = compute_file_hash(save_path)
            if local_hash == remote_hash:
                tqdm.write(f"✅ Skipped (unchanged): {os.path.basename(save_path)}")
                return "Skipped"

        os.makedirs(os.path.dirname(save_path), exist_ok=True)
        with open(save_path, "wb") as f:
            f.write(content)
        tqdm.write(f"⬇️  Downloaded: {os.path.basename(save_path)}")
        return "Downloaded"

    except Exception as e:
        tqdm.write(f"❌ Failed to download {url} - {e}")
        return "Error"

def process_champion(champ):
    session = requests.Session()
    try:
        res = session.get(f"{base_url}{champ}")
        res.raise_for_status()
        soup = BeautifulSoup(res.text, "html.parser")

        card = soup.find("div", class_="infobox champion-upd")
        if not card:
            tqdm.write(f"❌ No infobox found for {champ}")
            return

        table = card.find("table")
        spans = table.find_all("span")
        champ_name = spans[0].get_text(strip=True)
        champ_title = spans[1].get_text(strip=True)

        info_data = {
            "Champion": champ_name,
            "Title": champ_title
        }

        rows = card.find_all("div", class_="infobox-data-row championbox")
        for row in rows:
            label_tag = row.find("div", class_="infobox-data-label")
            value_tag = row.find("div", class_="infobox-data-value")
            if not label_tag or not value_tag:
                continue
            label = label_tag.get_text(strip=True)
            if label == "Last changed":
                continue
            value = " ".join(value_tag.stripped_strings)
            info_data[label] = value

        champ_dir = os.path.join(output_dir, champ_name)
        os.makedirs(champ_dir, exist_ok=True)

        # === Save info.csv ===
        info_csv_path = os.path.join(champ_dir, "info.csv")
        with open(info_csv_path, "w", newline="", encoding="utf-8") as f:
            writer = csv.DictWriter(f, fieldnames=info_data.keys())
            writer.writeheader()
            writer.writerow(info_data)

        # === Process skills ===
        skill_csv_data = []
        for skill in skills:
            try:
                div = soup.find("div", class_=skill)
                if not div:
                    continue

                skill_name_tag = div.find("div", class_="ability-info-stats__ability")
                if not skill_name_tag:
                    continue

                skill_name = skill_name_tag.get_text(strip=True)
                icon_divs = div.find_all("div", class_="ability-info-icon")

                for idx, icon_div in enumerate(icon_divs):
                    try:
                        img_tag = icon_div.find("img", src=True)
                        if not img_tag:
                            continue

                        src = img_tag['src'].split("?")[0]
                        full_url = urljoin(base_url, src)
                        ext = os.path.splitext(src)[1] or ".png"
                        safe_skill_name = sanitize(skill_name)
                        filename = f"{safe_skill_name}_{idx+1}{ext}"
                        save_path = os.path.join(champ_dir, "skills", filename)

                        status = download_image_if_not_exists(full_url, save_path, session)

                        skill_csv_data.append({
                            "Skill": skill_name,
                            "ImageFile": filename
                        })

                    except Exception as e:
                        tqdm.write(f"⚠️ Error processing image #{idx+1} for {skill_name} - {e}")

            except Exception as e:
                tqdm.write(f"⚠️ Error processing skill '{skill}' for {champ_name} - {e}")

        # === Save skills.csv ===
        if skill_csv_data:
            try:
                skill_csv_path = os.path.join(champ_dir, "skills.csv")
                with open(skill_csv_path, "w", newline="", encoding="utf-8") as f:
                    writer = csv.DictWriter(f, fieldnames=skill_csv_data[0].keys())
                    writer.writeheader()
                    writer.writerows(skill_csv_data)
            except Exception as e:
                tqdm.write(f"❌ Failed to write skills.csv for {champ_name} - {e}")

    except Exception as e:
        tqdm.write(f"❌ Error processing {champ}: {e}")

# === Run Multithreaded ===
with ThreadPoolExecutor(max_workers=MAX_THREADS) as executor:
    futures = [executor.submit(process_champion, champ) for champ in ChampionData]
    for future in tqdm(as_completed(futures), total=len(futures), desc="Processing Champions"):
        future.result()  # Ensures exceptions inside threads are raised here


Processing Champions:   0%|          | 0/171 [00:03<?, ?it/s]

⬇️  Downloaded: Drakehounds_Step_3.png


Processing Champions:   0%|          | 0/171 [00:04<?, ?it/s]

⬇️  Downloaded: Cunning_Sweep_1.png
⬇️  Downloaded: Cursed_Touch_1.png


Processing Champions:   0%|          | 0/171 [00:04<?, ?it/s]

...

⬇️  Downloaded: Chronoshift_1.png
⬇️  Downloaded: Hexplosive_Minefield_1.png
⬇️  Downloaded: More_Sparkles!_1.png
⬇️  Downloaded: Mega_Inferno_Bomb_1.png
⬇️  Downloaded: Paddle_Star!_1.png
⬇️  Downloaded: Mega_Inferno_Bomb_2.png
⬇️  Downloaded: Paddle_Star!_3.png
⬇️  Downloaded: Garden_of_Thorns_1.png


Processing Champions:  99%|█████████▉| 170/171 [02:02<00:00,  4.13it/s]

⬇️  Downloaded: Spell_Thief_1.png
⬇️  Downloaded: Spell_Thief_3.png
⬇️  Downloaded: Deadly_Spines_1.png
⬇️  Downloaded: Sleepy_Trouble_Bubble_1.png
⬇️  Downloaded: Rampant_Growth_1.png
⬇️  Downloaded: Portal_Jump_1.png
⬇️  Downloaded: Grasping_Roots_1.png


Processing Champions: 100%|██████████| 171/171 [02:02<00:00,  1.39it/s]

⬇️  Downloaded: Stranglethorns_1.png


Champions: 100%|██████████| 2/2 [00:01<00:00,  1.63it/s]
